In [220]:
import nibabel as nib
import numpy as np
import plotly.graph_objects as go
from scipy.ndimage import gaussian_filter
from scipy.spatial import cKDTree

In [221]:
def load_and_preprocess_nifti(nifti_path):
    print(f"Loading NIFTI file from {nifti_path}")
    nifti_img = nib.load(nifti_path)
    nifti_data = nifti_img.get_fdata()
    print("Normalizing data")
    normalized_data = (nifti_data - np.min(nifti_data)) / (np.max(nifti_data) - np.min(nifti_data))
    print("Data loaded and preprocessed")
    return normalized_data

In [222]:
def save_as_nrrd(data, file_path):
    """Save the numpy array as NRRD file."""
    nrrd.write(file_path, data)

def downsample_3d(data, factor):
    return data[::factor, ::factor, ::factor]

In [225]:
def compute_hog3d(ct_data, block_size=8, cell_size=4, stride=4, num_bins=12):
    print("Starting HOG3D computation")
    smoothed_data = gaussian_filter(ct_data, sigma=1)
    gx, gy, gz = np.gradient(smoothed_data)
    magnitude = np.sqrt(gx**2 + gy**2 + gz**2)
    phi = np.arctan2(np.sqrt(gx**2 + gy**2), gz)
    theta = np.arctan2(gy, gx)

    hog3d_features = []
    hog3d_positions = []
    hog3d_orientations = []

    total_blocks = ((ct_data.shape[0] - block_size) // stride + 1) * \
                   ((ct_data.shape[1] - block_size) // stride + 1) * \
                   ((ct_data.shape[2] - block_size) // stride + 1)
    current_block = 0

    for x in range(0, ct_data.shape[0] - block_size + 1, stride):
        for y in range(0, ct_data.shape[1] - block_size + 1, stride):
            for z in range(0, ct_data.shape[2] - block_size + 1, stride):
                block_hist = []
                block_phi = []
                block_theta = []
                block_magnitude = []

                for i in range(0, block_size, cell_size):
                    for j in range(0, block_size, cell_size):
                        for k in range(0, block_size, cell_size):
                            cell_phi = phi[x+i:x+i+cell_size, y+j:y+j+cell_size, z+k:z+k+cell_size]
                            cell_theta = theta[x+i:x+i+cell_size, y+j:y+j+cell_size, z+k:z+k+cell_size]
                            cell_magnitude = magnitude[x+i:x+i+cell_size, y+j:y+j+cell_size, z+k:z+k+cell_size]

                            hist, _ = np.histogramdd(
                                np.column_stack([cell_phi.ravel(), cell_theta.ravel()]),
                                bins=[num_bins, num_bins],
                                range=[[0, np.pi], [-np.pi, np.pi]],
                                weights=cell_magnitude.ravel()
                            )
                            block_hist.extend(hist.ravel())
                            
                            block_phi.extend(cell_phi.ravel())
                            block_theta.extend(cell_theta.ravel())
                            block_magnitude.extend(cell_magnitude.ravel())

                block_hist = np.array(block_hist)
                # Use L2-Hys normalization
                block_hist = np.clip(block_hist / np.sqrt(np.sum(block_hist**2) + 1e-6), 0, 0.2)
                block_hist = block_hist / np.sqrt(np.sum(block_hist**2) + 1e-6)

                hog3d_features.append(block_hist)
                hog3d_positions.append((x, y, z))

                # Compute mean orientation for the block
                block_magnitude = np.array(block_magnitude)
                if np.sum(block_magnitude) > 0:
                    mean_phi = np.average(block_phi, weights=block_magnitude)
                    mean_theta = np.average(block_theta, weights=block_magnitude)
                else:
                    # If all magnitudes are zero, set a default orientation
                    mean_phi = 0
                    mean_theta = 0
                hog3d_orientations.append((mean_phi, mean_theta))

                current_block += 1
                if current_block % 10000 == 0 or current_block == total_blocks:
                    print(f"Processed {current_block}/{total_blocks} blocks")

    print("HOG3D computation completed")
    return np.array(hog3d_features), np.array(hog3d_positions), np.array(hog3d_orientations)

In [250]:

from plotly.subplots import make_subplots


def visualize_hog3d(ct_data, hog3d_features, hog3d_positions, hog3d_orientations, threshold=0.75, save_path=None):
    print("Starting visualization")
    feature_magnitudes = np.linalg.norm(hog3d_features, axis=1)
    
    # Use a more discriminative threshold
    magnitude_threshold = np.percentile(feature_magnitudes, threshold * 100)
    mask = feature_magnitudes > magnitude_threshold
    
    filtered_positions = hog3d_positions[mask]
    filtered_magnitudes = feature_magnitudes[mask]
    filtered_orientations = hog3d_orientations[mask]
    
    # Apply non-linear transformation to magnitudes
    filtered_magnitudes = np.power(filtered_magnitudes, 0.3)  # Adjust the power for desired spread
    
    # Find the bounding box of important features
    min_x, min_y, min_z = np.min(filtered_positions, axis=0)
    max_x, max_y, max_z = np.max(filtered_positions, axis=0)
    
    # Add some padding to the bounding box
    padding = 10
    min_x, min_y, min_z = max(0, min_x - padding), max(0, min_y - padding), max(0, min_z - padding)
    max_x, max_y, max_z = min(ct_data.shape[0], max_x + padding), min(ct_data.shape[1], max_y + padding), min(ct_data.shape[2], max_z + padding)
    
    # Create subplots
    fig = make_subplots(
        rows=1, cols=3,
        specs=[[{'type': 'scene'}, {'type': 'scene'}, {'type': 'scene'}]],
        subplot_titles=("Feature Positions", "Orientations", "Combined")
    )
    
    # 1. Feature position points
    fig.add_trace(
        go.Scatter3d(
            x=filtered_positions[:, 0],
            y=filtered_positions[:, 1],
            z=filtered_positions[:, 2],
            mode='markers',
            marker=dict(
                size=1,
                color=filtered_magnitudes,
                colorscale='Viridis',
                opacity=1,
                colorbar=dict(title="Feature Magnitude", x=0.3)
            ),
            name='HOG3D Features'
        ),
        row=1, col=1
    )
    
    # 2. Orientation cones
    u = np.sin(filtered_orientations[:, 0]) * np.cos(filtered_orientations[:, 1])
    v = np.sin(filtered_orientations[:, 0]) * np.sin(filtered_orientations[:, 1])
    w = np.cos(filtered_orientations[:, 0])
    
    scale_factor = 5
    u *= scale_factor
    v *= scale_factor
    w *= scale_factor
    
    fig.add_trace(
        go.Cone(
            x=filtered_positions[:, 0],
            y=filtered_positions[:, 1],
            z=filtered_positions[:, 2],
            u=u,
            v=v,
            w=w,
            colorscale='Plotly3',
            sizemode="absolute",
            opacity=0.2,
            sizeref=3,
            
        ),
        row=1, col=2
    )
    
    # 3. Combined visualization
    fig.add_trace(
        go.Scatter3d(
            x=filtered_positions[:, 0],
            y=filtered_positions[:, 1],
            z=filtered_positions[:, 2],
            mode='markers',
            marker=dict(
                size=1,
                color=filtered_magnitudes,
                colorscale='Viridis',
                opacity=1,
                
            ),
            name='HOG3D Features'
        ),
        row=1, col=3
    )
    
    fig.add_trace(
        go.Cone(
            x=filtered_positions[:, 0],
            y=filtered_positions[:, 1],
            z=filtered_positions[:, 2],
            u=u,
            v=v,
            w=w,
            colorscale='Plotly3',
            sizemode="absolute",
            opacity=0.4,
            sizeref=5,
            
        ),
        row=1, col=3
    )
    
    # Update layout for all subplots
    for i in range(1, 4):
        fig.update_scenes(
            xaxis=dict(title="X", range=[min_x, max_x]),
            yaxis=dict(title="Y", range=[min_y, max_y]),
            zaxis=dict(title="Z", range=[min_z, max_z]),
            aspectmode='data',
            row=1, col=i
        )
    
    fig.update_layout(
        width=5000,
        height=1000,
        title="HOG3D Feature and Orientation Visualization (Cropped)"
    )
    
    fig.show()
    
    if save_path:
        fig.write_html(save_path)
        print(f"Visualization saved to {save_path}")
    
    print("Visualization completed")

In [228]:
nifti_file = "NIFTY/Img_001.nii.gz"  # Replace with the correct file path
ct_data = load_and_preprocess_nifti(nifti_file)

print("Processed data shape:", ct_data.shape)

downsample_factor = 2
downsampled_ct_data = downsample_3d(ct_data, downsample_factor)
print("Downsampled data shape:", downsampled_ct_data.shape)
# Assuming ct_data is your preprocessed and segmented CT data
hog3d_features, hog3d_positions, hog3d_orientations = compute_hog3d(ct_data, block_size=8, cell_size=4, stride=4, num_bins=12)
print("HOG3D features shape:", hog3d_features.shape)
print("HOG3D positions shape:", hog3d_positions.shape)
print("HOG3D orientations shape:", hog3d_orientations.shape)

Loading NIFTI file from NIFTY/Img_001.nii.gz
Normalizing data
Data loaded and preprocessed
Processed data shape: (512, 512, 275)
Downsampled data shape: (256, 256, 138)
Starting HOG3D computation
Processed 10000/1080643 blocks
Processed 20000/1080643 blocks
Processed 30000/1080643 blocks
Processed 40000/1080643 blocks
Processed 50000/1080643 blocks
Processed 60000/1080643 blocks
Processed 70000/1080643 blocks
Processed 80000/1080643 blocks
Processed 90000/1080643 blocks
Processed 100000/1080643 blocks
Processed 110000/1080643 blocks
Processed 120000/1080643 blocks
Processed 130000/1080643 blocks
Processed 140000/1080643 blocks
Processed 150000/1080643 blocks
Processed 160000/1080643 blocks
Processed 170000/1080643 blocks
Processed 180000/1080643 blocks
Processed 190000/1080643 blocks
Processed 200000/1080643 blocks
Processed 210000/1080643 blocks
Processed 220000/1080643 blocks
Processed 230000/1080643 blocks
Processed 240000/1080643 blocks
Processed 250000/1080643 blocks
Processed 260

In [251]:
# Visualize HOG3D features
from plotly.subplots import make_subplots
save_path = "hog3d_visualization.html"  # Set to None if you don't want to save
visualize_hog3d(ct_data, hog3d_features, hog3d_positions, hog3d_orientations, threshold=0.5, save_path=save_path)

Starting visualization


Visualization saved to hog3d_visualization.html
Visualization completed
